In [1]:
## Import necessary packages

%matplotlib qt
# On Macs use osx
# For Windows use qt

import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

In [2]:
def AddHill(Z,NX,NY,xx,yy,r,h):

    for x in range(1,100):
        for y in range(1,NY):
            dx = np.mod(x-xx+NX/2,NX)-NX; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/5,NY)-NY;
            dr = np.sqrt((dx**2)/2+(dy**2)/4);
            if (dr<r):
                Z[x,y] += h * (np.cos(dr/r*np.pi/2.0))*2 #4;
    return Z


In [3]:
### Define simulation grid and initial conditions

NX = 100*2 #number of rows
NY = 100*2 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

# small random features in topography to begin erosion
Z= rand(NX,NY)*.1

for i in range(150,200):
    xx = .2*NX
    yy = .2*NY
    r  = (0.5)*NX
    h  = (0.2)*2 #5
    Z = AddHill(Z,NX,NY,xx,yy,r,h)

for i in range (150,200):
    Z[150:200,1:NY]= 60*2 #200*2
    
for i in range (150,200): 
    Z[100:150,1:NY]= 40*2 #150*2
    




x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) #strange that y goes first !!!
ZMaxOrg = np.max(Z)
#print(ZMaxOrg)

In [4]:
### Physical Parameters
K = 1.0e-6 # meters^(1-2m)/yr

D = 0.005 # m^2/yr

# uplift rate
uplift = 1.2/1000

In [5]:
### Model parameters

# Time step
dt = d**2 / D / 100
#dt = d**2 / D /16. #extra small steps 
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=1

#gradient exponent g^n, default n=1
n=1

#erosion threshold 
theta_c = 10

 dt[years] =  50.0


In [6]:
# Total simulation time
T = 1000.0*40  #625

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of interation: ',n_iter)

Number of interation:  800


In [7]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.1  # what does this parameter do?
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           1.1779425527091992e-05
Maximum elevation           120.0
Beach level                 12.000010601482977
Ocean volume                108906.12671995815
Percentage of ocean surface 30.1875


In [8]:
# Set-up figure
from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

#       surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
#                antialiased=False,linewidth=0)

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        #ax2 = fig.add_subplot(122,aspect='equal')
        #ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        #im = ax2.pcolor(ZPlot,cmap=cm.terrain)
        #cs = ax2.contour(ZPlot,6,colors='k')

        # Add a color bar which maps values to colors.
        #cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        #cbar.add_lines(cs)

        #plt.show()
        plt.draw()
        plt.pause(0.0001)

In [9]:
# Set up figure
fig = init_figure()
update_figure()
Znew = np.copy(Z)
with writer.saving(fig, "MarineTerraceErosion.mp4", dpi=200):
    for it in range(1,n_iter+1):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,10)==0): 
            print(it,end='')
            update_figure()
            print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')
        fig.clear()
        update_figure()
        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()
    print(' Simulation finished.')

    
        

.........10 Ocean level= 18.000152340511345  Ocean surface fraction= 30.2425
.........20 Ocean level= 24.00011612384189  Ocean surface fraction= 30.305
.........30 Ocean level= 29.999968550488962  Ocean surface fraction= 30.35
.........40 Ocean level= 35.99996319146913  Ocean surface fraction= 30.3875
.........50 Ocean level= 41.99996319146914  Ocean surface fraction= 30.42
.........60 Ocean level= 47.999963191469156  Ocean surface fraction= 30.4525
.........70 Ocean level= 53.99990477175665  Ocean surface fraction= 30.495
.........80 Ocean level= 59.999889758520396  Ocean surface fraction= 30.5275
.........90 Ocean level= 65.99988307707903  Ocean surface fraction= 30.56
.........100 Ocean level= 71.99988307707898  Ocean surface fraction= 30.585
.........110 Ocean level= 77.99988307707892  Ocean surface fraction= 30.615
.........120 Ocean level= 83.99985253923754  Ocean surface fraction= 30.6525
.........130 Ocean level= 89.99985253923748  Ocean surface fraction= 30.67
.........140 Oce